# COVID-19 Data Analysis

In [1]:
import numpy as np 
import pandas as pd 



**<font color = DarkSlateBlue size = 5 >Table of Contents</font>**

* [**<font color = SteelBlue size = 4>Import related libraries</font>**](#section-one)

* [**<font color = SteelBlue size = 4>Read data and Inspect data</font>**](#section-two)

* [**<font color = SteelBlue size = 4>Data Cleaning</font>**](#section-three)

* [**<font color = SteelBlue size = 4>Data Analysis - World</font>**](#section-four)
    - [**<font color = CornflowerBlue size = 4>Summay - World</font>**](#subsection-one)
* [**<font color = SteelBlue size = 4>Data Analysis - United States of America</font>**](#section-five)
    - [**<font color = CornflowerBlue size = 4>Summary - United States of America</font>**](#subsection-two)
* [**<font color = SteelBlue size = 4>Data Analysis - China</font>**](#section-six)
    - [**<font color = CornflowerBlue size = 4>Summary - China</font>**](#subsection-three)
* [**<font color = SteelBlue size = 4>Data Analysis - United Kingdom</font>**](#section-seven)
    - [**<font color = CornflowerBlue size = 4>Summary - United Kingdom</font>**](#subsection-four)


<a id="section-one"></a>
**<font color = Blue size = 5>Import related libraries</font>**

In [2]:
import numpy as np
import pandas as pd
import plotly.graph_objs as go
import plotly.express as px 
from pandas_profiling import ProfileReport
from datetime import datetime

<a id="section-two"></a>
**<font color = Blue size = 5>Read data and Inspect data</font>**

In [3]:
# Read data
df = pd.read_csv('resources/covid_19_data.csv')

In [4]:
# Show first five rows of data
df.head()

SNo ObservationDate Province/State  Country/Region      Last Update  \
0    1      01/22/2020          Anhui  Mainland China  1/22/2020 17:00   
1    2      01/22/2020        Beijing  Mainland China  1/22/2020 17:00   
2    3      01/22/2020      Chongqing  Mainland China  1/22/2020 17:00   
3    4      01/22/2020         Fujian  Mainland China  1/22/2020 17:00   
4    5      01/22/2020          Gansu  Mainland China  1/22/2020 17:00   

   Confirmed  Deaths  Recovered  
0        1.0     0.0        0.0  
1       14.0     0.0        0.0  
2        6.0     0.0        0.0  
3        1.0     0.0        0.0  
4        0.0     0.0        0.0

In [5]:
# Information about data
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 306429 entries, 0 to 306428
Data columns (total 8 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   SNo              306429 non-null  int64  
 1   ObservationDate  306429 non-null  object 
 2   Province/State   228329 non-null  object 
 3   Country/Region   306429 non-null  object 
 4   Last Update      306429 non-null  object 
 5   Confirmed        306429 non-null  float64
 6   Deaths           306429 non-null  float64
 7   Recovered        306429 non-null  float64
dtypes: float64(3), int64(1), object(4)
memory usage: 18.7+ MB


In [6]:
# Pandas Profiling
rep = ProfileReport(df)
rep

Render HTML: 100%|██████████| 1/1 [00:01<00:00,  1.16s/it]


<a id="section-three"></a>
**<font color = Green size = 5>Data Cleaning</font>**

In [7]:
df['Province/State'] = df['Province/State'].fillna("Unknown")

In [8]:
df.isnull().sum()

SNo                0
ObservationDate    0
Province/State     0
Country/Region     0
Last Update        0
Confirmed          0
Deaths             0
Recovered          0
dtype: int64

In [9]:
df = df.rename(columns = {"Province/State":"State"})
df = df.rename(columns = {"Country/Region":"Country"})

In [10]:
df[['Confirmed','Deaths','Recovered']] = df[['Confirmed','Deaths','Recovered']].astype(int)

In [11]:
df['Active'] = df['Confirmed']-df['Deaths']-df['Recovered']
df.columns

Index(['SNo', 'ObservationDate', 'State', 'Country', 'Last Update',
       'Confirmed', 'Deaths', 'Recovered', 'Active'],
      dtype='object')

In [12]:
df['Date'] = df['ObservationDate'].copy()

<a id="section-four"></a>
**<font color = Blue size = 5>Data Analysis📊</font>**

**<font color = red size = 4>Covid-19 Cases in the World🌎</font>**

In [13]:
fig = go.Figure(data = [go.Table(
    header = dict(
        values = ['<b>Total Confirmed</b>','<b>Total Deaths</b>','<b>Total Recovered</b>','<b>Total Active Cases</b>'],
        line_color='darkslategray',
        fill_color= 'DarkCyan',
        align='center',
        font=dict(color='white', size=12)
    ),
    cells = dict(
        values = [sum(df['Confirmed']),sum(df['Deaths']),sum(df['Recovered']),sum(df['Active'])],
        line_color='darkslategray',
        fill_color = 'white',
        font = dict(color = 'darkslategray', size = 11))
)])

fig.update_layout(title = 'World-Covid-19 Cases',
                  title_x = 0.5,
                  title_font = dict(size = 16, color = 'DarkCyan'))

fig.show()

In [14]:
labels = ["Active Cases","Recovered Cases","Death Cases"]

sumactive= sum(df['Active'])
sumrecoverd = sum(df['Recovered'])
sumdeaths = sum(df['Deaths'])

fig = px.pie(df, 
             values = [sumactive,sumrecoverd,sumdeaths],
             names = labels,
             color_discrete_sequence = ['SkyBlue','PaleGreen','LightSlateGray'])

fig.update_traces(textposition = 'inside', textinfo = 'percent+label')

fig.update_layout(title = 'The percentage of Covid-19 Cases in the world',
                  title_x = 0.5,
                  title_font= dict(size = 18, color = 'MidnightBlue' ))

fig.show()

In [15]:
df['Date'] = pd.to_datetime(df['Date'])
df = df.sort_values("Date")

In [16]:
dftime = df.groupby("Date")[["Confirmed","Active","Recovered","Deaths"]].sum().reset_index()

In [17]:
fig = px.bar(dftime,
             x = 'Date',
             y = 'Confirmed',
             color = 'Confirmed',
             color_continuous_scale = 'rdpu',
             labels = {"Confirmed":"Confirmed Cases"})

fig.update_layout(title = 'Confirmed Cases - Daily',
                  title_x = 0.5,
                  title_font = dict(size= 18, color = 'Purple'),
                  xaxis = dict(title = 'Date'),
                  yaxis = dict(title = 'Confirmed Cases'))

fig.show()

In [18]:
fig = px.bar(dftime,
             x = 'Date',
             y = 'Recovered',
             color = 'Recovered',
             color_continuous_scale = 'greens',
             labels = {"Recovered":"Recovered Cases"})

fig.update_layout(title = 'Recovered Cases - Daily',
                  title_x = 0.5,
                  title_font = dict(size= 18, color = 'DarkGreen'),
                  xaxis = dict(title = 'Date'),
                  yaxis = dict(title = 'Recovered Cases'))

fig.show()

In [19]:
fig = px.bar(dftime,
             x = 'Date',
             y = 'Active',
             color = 'Active',
             color_continuous_scale = 'blues',
             labels = {"Active":"Active Cases"})

fig.update_layout(title = 'Active Cases - Daily',
                  title_x = 0.5,
                  title_font = dict(size= 18, color = 'DarkBlue'),
                  xaxis = dict(title = 'Date'),
                  yaxis = dict(title = 'Active Cases'))

fig.show()

In [20]:
fig = px.bar(dftime,
             x = 'Date',
             y = 'Deaths',
             color = 'Deaths',
             color_continuous_scale = 'gray',
             labels = {"Deaths":"Death Caaes"})

fig.update_layout(title = 'Death Cases - Daily',
                  title_x = 0.5,
                  title_font = dict(size= 18, color = 'DarkSlateGray'),
                  xaxis = dict(title = 'Date'),
                  yaxis = dict(title = 'Death Cases'))

fig.show()

In [21]:
df1 = df.groupby("Country")["Confirmed"].sum().sort_values(ascending = False).reset_index().head(30)

fig = px.bar(df1,
             x = 'Country',
             y = 'Confirmed',
             color = 'Confirmed',
             color_continuous_scale = 'rdpu',
             labels = {"Confirmed":"Confirmed Cases"})

fig.update_layout(title = 'Top 30 Countries with the most Confirmed Cases',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'Purple'),
                  yaxis = dict(title = 'Confirmed Cases'),
                  xaxis = dict(tickangle = 45))
fig.show()

In [22]:
df1 = df.groupby("Country")["Active"].sum().sort_values(ascending = False).reset_index().head(30)

fig = px.bar(df1,
             x = 'Country',
             y = 'Active',
             color = 'Active',
             color_continuous_scale = 'blues',
             labels = {"Active":"Active Cases"})

fig.update_layout(title = 'Top 30 Countries with the most Active Cases',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkBlue'),
                  yaxis = dict(title = 'Active Cases'),
                  xaxis = dict(tickangle = 45))

fig.show()

In [23]:
df1 = df.groupby("Country")["Recovered"].sum().sort_values(ascending = False).reset_index().head(30)

fig = px.bar(df1,
             x = 'Country',
             y = 'Recovered',
             color = 'Recovered',
             color_continuous_scale = 'greens',
             labels = {"Confirmed":"Recovered Cases"})

fig.update_layout(title = 'Top 30 Countries with the most Recovered Cases',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkGreen'),
                  yaxis = dict(title = 'Recovered Cases'),
                  xaxis = dict(tickangle = 45))

fig.show()

In [24]:
df1 = df.groupby("Country")["Deaths"].sum().sort_values(ascending = False).reset_index().head(30)

fig = px.bar(df1,
             x = 'Country',
             y = 'Deaths',
             color = 'Deaths',
             color_continuous_scale = 'gray',
             labels = {"Deaths":"Death Cases"})

fig.update_layout(title = 'Top 30 Countries with the most Death Cases',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkSlateGray'),
                  yaxis = dict(title = 'Death Cases'),
                  xaxis = dict(tickangle = 45))

fig.show()

**<font color = Darkred size = 4>World - Map</font>**

In [25]:
df1 = df.groupby("Country")["Confirmed"].sum().sort_values(ascending = False).reset_index()

fig = px.choropleth(df1, 
                    locations = 'Country',
                    locationmode = 'country names',
                    color = 'Confirmed',
                    hover_name = 'Country',
                    color_continuous_scale= 'rdpu',
                    labels = {"Confirmed":"Confirmed Cases"},
                    animation_frame = 'Country')

fig.update_layout(title = 'World - Confirmed Cases by Countries',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'Purple'),
                  geo = dict(showframe = False,
                             showcoastlines = False,
                             projection_type = 'equirectangular'
                            ))
fig.show()

In [26]:
df1 = df.groupby("Country")[["Confirmed","Active","Recovered","Deaths"]].sum().sort_values("Confirmed",ascending=False).reset_index()

fig = px.choropleth(df1, 
                    locations = 'Country',
                    locationmode = 'country names',
                    color = 'Confirmed',
                    hover_name = 'Country',
                    color_continuous_scale = 'twilight',
                    hover_data = ["Active","Recovered","Deaths"])

fig.update_layout(title = 'World - Covid-19 Cases',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'Darkblue'),
                  geo = dict(showframe = False,
                             showcoastlines = False,
                             projection_type = 'equirectangular'
                            ))
fig.show()

In [27]:
df['Year'] = df['ObservationDate'].apply(lambda x : x.split("/")[-1])
df.head()

SNo ObservationDate     State         Country      Last Update  Confirmed  \
0     1      01/22/2020     Anhui  Mainland China  1/22/2020 17:00          1   
22   23      01/22/2020   Qinghai  Mainland China  1/22/2020 17:00          0   
23   24      01/22/2020   Shaanxi  Mainland China  1/22/2020 17:00          0   
24   25      01/22/2020  Shandong  Mainland China  1/22/2020 17:00          2   
25   26      01/22/2020  Shanghai  Mainland China  1/22/2020 17:00          9   

    Deaths  Recovered  Active       Date  Year  
0        0          0       1 2020-01-22  2020  
22       0          0       0 2020-01-22  2020  
23       0          0       0 2020-01-22  2020  
24       0          0       2 2020-01-22  2020  
25       0          0       9 2020-01-22  2020

In [28]:
df2020 = df[df['Year']=='2020']
df1 = df2020.groupby(["Country","ObservationDate"])["Confirmed"].sum().reset_index().sort_values("ObservationDate",ascending=True).reset_index()

fig = px.choropleth(df1, 
                    locations = 'Country',
                    locationmode = 'country names',
                    color = 'Confirmed',
                    hover_name = 'Country',
                    color_continuous_scale= 'plasma',
                    labels = {"Confirmed":"Confirmed Cases","ObservationDate":"Date"},
                    animation_frame = 'ObservationDate')

fig.update_layout(title = 'World - Confirmed Cases by date in 2020',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'Darkblue'),
                  geo = dict(showframe = False,
                             showcoastlines = False,
                             projection_type = 'equirectangular'
                            ))
fig.show()

In [29]:
df2021 = df[df['Year']=='2021']
df1 = df2021.groupby(["Country","ObservationDate"])["Confirmed"].sum().reset_index().sort_values("ObservationDate",ascending=True).reset_index()

fig = px.choropleth(df1, 
                    locations = 'Country',
                    locationmode = 'country names',
                    color = 'Confirmed',
                    hover_name = 'Country',
                    color_continuous_scale= 'plasma',
                    labels = {"Confirmed":"Confirmed Cases","ObservationDate":"Date"},
                    animation_frame = 'ObservationDate')

fig.update_layout(title = 'World - Confirmed Cases by date in 2021',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'Darkblue'),
                  geo = dict(showframe = False,
                             showcoastlines = False,
                             projection_type = 'equirectangular'
                            ))
fig.show()

<a id="subsection-one"></a>
**<font color = Teal size = 4 >Summary</font>**

**Until the end of May 2021, total confirmed cases is nearly 27 billion. The number of deaths is about 600 million. Some charts shows that the confirmed cases, deaths and Recovered cases are significantly increased from 2020 to the end of May 2021. As we can see there is an increasing trend. Additionally, through some bar charts, we can see top countries with the most confirmed cases are the countries with large population, which are United States, India and Brazil respectively.**

<a id="section-five"></a>
**<font color = red size = 4>Covid-19 Cases in the United States</font>**

In [30]:
dfus = df[(df['Country'] == 'US') ].reset_index()

In [31]:
fig = go.Figure(data = [go.Table(
    header = dict(
        values = ['<b>Total Confirmed</b>','<b>Total Deaths</b>','<b>Total Recovered</b>','<b>Total Active Cases</b>'],
        line_color='darkslategray',
        fill_color= 'DarkRed',
        align='center',
        font=dict(color='white', size=12)
    ),
    cells = dict(
        values = [sum(dfus['Confirmed']),sum(dfus['Deaths']),sum(dfus['Recovered']),sum(dfus['Active'])],
        line_color='darkslategray',
        fill_color = 'white',
        font = dict(color = 'darkslategray', size = 12))
)])

fig.update_layout(title = 'US - Covid-19 Cases',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkRed'))

fig.show()

In [32]:
labels = ["Active Cases","Recovered Cases","Deaths"]

sumactive= sum(dfus['Active'])
sumrecoverd = sum(dfus['Recovered'])
sumdeaths = sum(dfus['Deaths'])

fig = px.pie(df, 
             values = [sumactive,sumrecoverd,sumdeaths],
             names = labels,
             color_discrete_sequence = ['SkyBlue','PaleGreen','LightSlateGray'])

fig.update_traces(textposition = 'inside', textinfo = 'percent+label')

fig.update_layout(title = 'The percentage of Covid-19 Cases in the United States',
                  title_x = 0.5,
                  title_font= dict(size = 18, color = 'MidnightBlue' ))

fig.show()

In [33]:
Data_US= dfus.groupby("Date")["Confirmed","Deaths","Recovered","Active"].sum().reset_index().sort_values("Date").reset_index()

fig = go.Figure()

fig.add_trace(go.Scatter(x=Data_US['Date'], 
                         y=Data_US['Confirmed'],
                         mode='lines',
                         name='Confirmed Cases',
                         marker_color='purple'))

fig.add_trace(go.Scatter(x=Data_US['Date'], 
                         y=Data_US['Active'],
                         mode='lines',
                         name='Active Cases',
                         marker_color='RoyalBlue',
                         line=dict( dash='dot')))

fig.add_trace(go.Scatter(x=Data_US['Date'], 
                         y=Data_US['Deaths'],
                         name='Death Cases',
                         marker_color='DarkSlateGray',
                         mode='lines',
                         line=dict( dash='dot') ))

fig.add_trace(go.Scatter(x=Data_US['Date'], 
                         y=Data_US['Recovered'],
                         mode='lines',
                         name='Recovered Cases',
                         marker_color='green'))

fig.update_layout(title='Covid-19 Cases over the time in the United States',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkSlateGray'),
                  template='plotly_white')

fig.show()

/tmp/ipykernel_31422/524797393.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [34]:
State_us= dfus.groupby(["State"])["Confirmed","Active","Deaths"].sum().sort_values("Confirmed",ascending=False).reset_index().head(20)

fig = px.bar(State_us,
             x = 'State',
             y = 'Confirmed',
             color = 'Confirmed',
             color_continuous_scale = 'rdpu')

fig.update_layout(title = 'Top 20 States with the most Confirmed Cases in the United States',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'Purple'),
                  xaxis = dict(tickangle = 45),
                  yaxis = dict(title = 'Confirmed Cases'))

fig.show()


/tmp/ipykernel_31422/4075787516.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [35]:
State_us= dfus.groupby(["State"])["Confirmed","Active","Deaths"].sum().sort_values("Active",ascending=False).reset_index().head(20)

fig = px.bar(State_us,
             x = 'State',
             y = 'Active',
             color = 'Active',
             color_continuous_scale = 'blues')

fig.update_layout(title = 'Top 20 States with the most Active Cases in the United States',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkBlue'),
                  xaxis = dict(tickangle = 45),
                  yaxis = dict(title = 'Active Cases'))

fig.show()

/tmp/ipykernel_31422/3795138095.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [36]:
State_us= dfus.groupby(["State"])["Confirmed","Active","Deaths"].sum().sort_values("Deaths",ascending=False).reset_index().head(20)

fig = px.bar(State_us,
             x = 'State',
             y = 'Deaths',
             color = 'Deaths',
             color_continuous_scale = 'gray')

fig.update_layout(title = 'Top 20 States with the most Death Cases in the United States',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkSlateGray'),
                  xaxis = dict(tickangle = 45),
                  yaxis = dict(title = 'Death Cases'))

fig.show()

/tmp/ipykernel_31422/964250042.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



<a id="subsection-two"></a>
**<font color = Teal size = 4 >Summary</font>**

**Total confirmed cases is more than 6 billion and the number of deaths is about 30 million until 29 May, 2021. In the united Stated, the number of confirmed cases is increased rapidly since September 2020, but it is increased slowly since February 2021. California, Texas and Florida are the states with the most confirmed cases in the United States. However, New York State was the state with the most deaths.**

<a id="section-six"></a>
**<font color = red size = 4>Covid-19 Cases in China</font>**

In [37]:
df['Country'] = df['Country'].replace('Mainland China', 'China')

In [38]:
dfch = df[(df['Country'] == 'China') ].reset_index()

In [39]:
fig = go.Figure(data = [go.Table(
    header = dict(
        values = ['<b>Total Confirmed</b>','<b>Total Deaths</b>','<b>Total Recovered</b>','<b>Total Active Cases</b>'],
        line_color='darkslategray',
        fill_color= 'FireBrick',
        align='center',
        font=dict(color='white', size=12)
    ),
    cells = dict(
        values = [sum(dfch['Confirmed']),sum(dfch['Deaths']),sum(dfch['Recovered']),sum(dfch['Active'])],
        line_color='darkslategray',
        fill_color = 'white',
        font = dict(color = 'darkslategray', size = 12))
)])

fig.update_layout(title = 'China - Covid-19 Cases',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'FireBrick'))

fig.show()

In [40]:
labels = ["Active Cases","Recovered Cases","Deaths"]

sumactive= sum(dfch['Active'])
sumrecoverd = sum(dfch['Recovered'])
sumdeaths = sum(dfch['Deaths'])

fig = px.pie(df, 
             values = [sumactive,sumrecoverd,sumdeaths],
             names = labels,
             color_discrete_sequence = ['SkyBlue','PaleGreen','LightSlateGray'])

fig.update_traces(textposition = 'inside', textinfo = 'percent+label')

fig.update_layout(title = 'The percentage of Covid-19 Cases in China',
                  title_x = 0.5,
                  title_font= dict(size = 18, color = 'MidnightBlue' ))

fig.show()

In [41]:
Data_CH= dfch.groupby("Date")["Confirmed","Deaths","Recovered","Active"].sum().reset_index().sort_values("Date").reset_index()

fig = go.Figure()

fig.add_trace(go.Scatter(x=Data_CH['Date'], 
                         y=Data_CH['Confirmed'],
                         mode='lines',
                         name='Confirmed Cases',
                         marker_color='purple'))

fig.add_trace(go.Scatter(x=Data_CH['Date'], 
                         y=Data_CH['Active'],
                         mode='lines',
                         name='Active Cases',
                         marker_color='RoyalBlue',
                         line=dict( dash='dot')))

fig.add_trace(go.Scatter(x=Data_CH['Date'], 
                         y=Data_CH['Deaths'],
                         name='Death Cases',
                         marker_color='DarkSlateGray',
                         mode='lines',
                         line=dict( dash='dot') ))

fig.add_trace(go.Scatter(x=Data_CH['Date'], 
                         y=Data_CH['Recovered'],
                         mode='lines',
                         name='Recovered Cases',
                         marker_color='green'))

fig.update_layout(title='Covid-19 Cases over the time in the China',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkSlateGray'),
                  template='plotly_white')

fig.show()

/tmp/ipykernel_31422/1156057122.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [42]:
State_ch= dfch.groupby(["State"])["Confirmed","Active","Deaths"].sum().sort_values("Confirmed",ascending=False).reset_index()

fig = px.pie(State_ch,
             values = 'Confirmed',
             names = 'State',
             hole = 0.3,
             color_discrete_sequence = px.colors.sequential.Rainbow
            
            )

fig.update_traces(textposition='inside', textinfo='percent+label')

fig.update_layout(title = 'Confirmed Cases in China by States',
                  title_font = dict(size = 16, color = 'Darkblue'))

fig.show()

/tmp/ipykernel_31422/2901633176.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [43]:
State_ch= dfch.groupby(["State"])["Confirmed","Active","Deaths"].sum().sort_values("Active",ascending=False).reset_index()

fig = px.pie(State_ch,
             values = 'Active',
             names = 'State',
             hole = 0.3,
             color_discrete_sequence = px.colors.sequential.Rainbow)

fig.update_traces(textposition='inside', textinfo='percent+label')

fig.update_layout(title = 'Active Cases in China by States',
                  title_font = dict(size = 16, color = 'Darkblue'))

fig.show()

/tmp/ipykernel_31422/323356915.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [44]:
State_ch= dfch.groupby(["State"])["Confirmed","Active","Deaths"].sum().sort_values("Deaths",ascending=False).reset_index()

fig = px.pie(State_ch,
             values = 'Deaths',
             names = 'State',
             hole = 0.3,
             color_discrete_sequence = px.colors.sequential.Rainbow)

fig.update_traces(textposition='inside', textinfo='percent+label')

fig.update_layout(title = 'Death Cases in China by States',
                  title_font = dict(size = 16, color = 'Darkblue'))

fig.show()

/tmp/ipykernel_31422/745392329.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



<a id="subsection-three"></a>
**<font color = Teal size = 4 >Summary</font>**

**The population of China is much larger than United States, but the number of confirmed cases in China is more than 40 million which is lower than in the United Stated. In contrast to the United States, the confirmed cases in China are significantly increased from Jan 2020 to March 2020, and it was not increased significantly from Mach 2020. In addition, top state with the most confirmed cases is Hubei, the total confirmed cases is much higher than the other States in China.**

<a id="section-seven"></a>
**<font color = red size = 4>Covid-19 Cases in the UK</font>**

In [45]:
dfuk = df[df['Country']=='UK'].reset_index()

In [46]:
fig = go.Figure(data = [go.Table(
    header = dict(
        values = ['<b>Total Confirmed</b>','<b>Total Deaths</b>','<b>Total Recovered</b>','<b>Total Active Cases</b>'],
        line_color='darkslategray',
        fill_color= 'DarkBlue',
        align='center',
        font=dict(color='white', size=12)
    ),
    cells = dict(
        values = [sum(dfuk['Confirmed']),sum(dfuk['Deaths']),sum(dfuk['Recovered']),sum(dfuk['Active'])],
        line_color='darkslategray',
        fill_color = 'white',
        font = dict(color = 'darkslategray', size = 12))
)])

fig.update_layout(title = 'UK - Covid-19 Cases',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkBlue'))

fig.show()

In [47]:
labels = ["Active Cases","Recovered Cases","Death Cases"]

sumactive= sum(dfuk['Active'])
sumrecoverd = sum(dfuk['Recovered'])
sumdeaths = sum(dfuk['Deaths'])

fig = px.pie(df, 
             values = [sumactive,sumrecoverd,sumdeaths],
             names = labels,
             color_discrete_sequence = ['SkyBlue','PaleGreen','LightSlateGray'])

fig.update_traces(textposition = 'inside', textinfo = 'percent+label')

fig.update_layout(title = 'The percentage of Covid-19 Cases in the UK',
                  title_x = 0.5,
                  title_font= dict(size = 18, color = 'MidnightBlue' ))

fig.show()

In [48]:
Data_UK= dfuk.groupby("Date")["Confirmed","Deaths","Recovered","Active"].sum().reset_index().sort_values("Date").reset_index()

fig = go.Figure()

fig.add_trace(go.Scatter(x=Data_UK['Date'], 
                         y=Data_UK['Confirmed'],
                         mode='lines',
                         name='Confirmed Cases',
                         marker_color='purple'))

fig.add_trace(go.Scatter(x=Data_UK['Date'], 
                         y=Data_UK['Active'],
                         mode='lines',
                         name='Active Cases',
                         marker_color='RoyalBlue',
                         line=dict( dash='dot')))

fig.add_trace(go.Scatter(x=Data_UK['Date'], 
                         y=Data_UK['Deaths'],
                         name='Death Cases',
                         marker_color='DarkSlateGray',
                         mode='lines',
                         line=dict( dash='dot') ))

fig.add_trace(go.Scatter(x=Data_UK['Date'], 
                         y=Data_UK['Recovered'],
                         mode='lines',
                         name='Recovered Cases',
                         marker_color='green'))

fig.update_layout(title='Covid-19 Cases over the time in the UK',
                  title_x = 0.5,
                  title_font = dict(size = 18, color = 'DarkSlateGray'),
                  template='plotly_white')

fig.show()

/tmp/ipykernel_31422/1764180864.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



<a id="subsection-four"></a>
**<font color = Teal size = 4 >Summary</font>**

**Total confirmed cases in the UK is nearly 800 million until the end of May 2021.
The number of deaths is about 30 million. The confirmed cases are significantly increased from September 2020 to February 2021. However, the trend of deaths is not outstandingly increased. From February 2021, the number of confirmed cases is slowly increased.**


**<font color = DarkBlue size = 5>Thank you for reading!😃</font>**

**Please consider upvoting & checking out more of my work if you found this interesting & valuable! Thanks so much!**